# Summarizer
This script is used for summarizing Czech news texts as well as for generating news headlines or abstracts. It can be considered as a demonstration for the application of our summarization models.


In [1]:
#dependencies
import torch as pt
import numpy as np

from collections import OrderedDict

from transformers import AutoModelForSeq2SeqLM
from transformers import  AutoTokenizer

from sentence_splitter import SentenceSplitter, split_text_into_sentences

#init Summarizer
#comment cuda and delete .to(cuda) if using cpuUse
class Summarizer:
    def __init__(self,model, tokenizer, inference_cfg):
        self.model = model
        self.model.cuda()
        self.tokenizer = tokenizer
        self.inference_cfg = inference_cfg
        self.enc_max_len = 512
    
    #tokenize & summarize input texts
    def __call__(self, texts, inference_cfg=None):
        if type(texts) == str:
            texts = [texts]
        assert type(texts) == list and type(texts[0]) == str, "Expected string or list of strings"
        summaries = []
        self.inference_cfg = inference_cfg if inference_cfg is not None else self.inference_cfg
        for text in texts:
            text = self.tokenizer.eos_token.join(SentenceSplitter(language='cs').split(text))
            ttext = self.tokenizer(text,max_length = self.enc_max_len, truncation=True, padding="max_length",return_tensors="pt")
            summaries.append(self._summarize(ttext,**self.inference_cfg)[0])
        return summaries
    
    #summarize batch of data
    def _summarize(self, data, num_beams=1, do_sample=False, 
                    top_k=50, 
                    top_p=1.0,
                    temperature=1.0,
                    repetition_penalty=1.0,
                    no_repeat_ngram_size = None,
                    max_length=1024,
                    min_length=10,
                    decode_decoder_ids = False,
                    early_stopping = False,**kwargs):
        summary = model.generate(input_ids=data["input_ids"].to("cuda"),attention_mask=data["attention_mask"].to("cuda"),
                                    num_beams= num_beams,
                                   do_sample= do_sample,
                                   top_k=top_k,
                                   top_p=top_p,
                                   temperature=temperature,
                                   repetition_penalty=repetition_penalty,
                                   max_length=max_length,
                                   min_length=min_length,
                                   early_stopping=early_stopping,
                                 forced_bos_token_id=tokenizer.lang_code_to_id['cs_CZ'])
        return self.tokenizer.batch_decode(summary,skip_special_tokens=True)




# Use
- Load Czech summarization model from https://huggingface.co/krotima1
- Summarize Czech news texts
- Play with summarization parameters

In [ ]:
# Summarization config, setting up hyperparameters of inference methods used during summarization
def summ_config():
    cfg = OrderedDict([
        # summarization model - checkpoint from website https://huggingface.co/krotima1
        ("model_name", "krotima1/mbart-at2h-c"),
        
        #inference configuration of summ parameters
        ("inference_cfg", OrderedDict([
            ("num_beams", 4),
            ("top_k", 40),
            ("top_p", 0.92),
            ("do_sample", True),
            ("temperature", 0.89),
            ("repetition_penalty", 1.2),
            ("no_repeat_ngram_size", None),
            ("early_stopping", True),
        #     ("max_length", 96),
            ("min_length", 10),
        ])),
        #texts to summarize
        ("text",
            [
                "Input your Czech text",
            ]
        ),
    ])
    return cfg
cfg = summ_config()
#load model & tokenizer
model = AutoModelForSeq2SeqLM.from_pretrained(cfg["model_name"])
tokenizer = AutoTokenizer.from_pretrained(cfg["model_name"])
#init summarizer
summarize = Summarizer(model, tokenizer, cfg["inference_cfg"])
#summarize Czech texts - jdem na to
#cfg["text"]=...
summarize(cfg["text"])

Downloading:   0%|          | 0.00/480 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/8.66M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/495 [00:00<?, ?B/s]

#### Change text to summarize

In [ ]:
cfg["text"] = "Nováčci, které stvořila soutěž Česko hledá SuperStar, vstoupí do konkurence s osvědčenými jmény domácího trhu. Jedním z nich je Lucie Bílá, která vydá kolekci hitů nazvanou Láska je láska. Naopak její kolegyně Anna K. bude mít zbrusu nové písně. Styl alba Anna K.: Noc na zemi prý připomíná rockový nářez s místy až mrazivým soundem.\nDo společnosti hvězd se vypracoval drsný zpěvák Daniel Landa, jehož album Neofolk vyjde začátkem října. \"Na desce jsou písničky, které zdáli folk připomínají. Více než dříve kladu důraz na jejich texty. Neofolk mi přijde jako větší vykřičník a jistě i zlobivější název. Jinak je to bigbít i folk. Po obsahu,\" míní Landa, který pracuje na dvou muzikálech. Navíc v listopadu vydá záznam z vyšehradského koncertu, na kterém zpíval písně Karla Kryla.\nKarel Plíhal si zase oblíbil básníka Josefa Kainara, jemuž vzdává hold na desce Nebe na zemi. Práce na tomto dlouho odkládaném a několikrát ohlašovaném albu se protáhly na šest let. Za tu dobu Plíhal nastudoval Kainarovu tvorbu a našel způsob, kterým by ji nejlépe vyjádřil. Stačí mu k tomu kytara, hlas a hostující zpěvačka Zuzana Navarová.\nPetr Muk si vybral jiné oblíbence: britskou kapelu Erasure, se kterou kdysi jako vokalista kapely Oceán odehrál 27 koncertů ve Velké Británii a Irsku. Na minialbu Oh L\"Amour chce Muk představit některé jejich písně.\nKoncem září se objeví novinka kapely Kryštof. Třetí album Mikrokosmos vznikalo pod dohledem Jana P. Muchowa, který si přál, aby kryštofovská muzika zněla maximálně živě, bez elektronických či jiných efektů. Hit Srdce, který se dostal do vysílání hudební televize MTV, byl vybrán jako propagační píseň.\nŘíká se, že třetí album je rozhodující. Přesvědčí se o tom i kapela MIG 21, soustředěná kolem herce a zpěváka Jiřího Macháčka. Jejich nová deska Pop Pop Pop ukazuje směr, kterým MIG 21 poletí. Méně se ví o listopadovém albu Midlife skupiny Support Lesbiens, která letos propustila kytaristu a skladatele Yardu Helešice a buduje nový hudební profil.\nRuku v ruce s nástupem hudebních DVD přibudou tituly bratří Ebenů, kapel Divokej Bill, Monkey Business nebo Kabát. Teplická formace se chce ohlédnout za dvěma masivními turné let 2003 a 2004, která jí zajistila postavení nejžádanější skupiny v Česku."

#### summarize

In [ ]:
summarize(cfg["text"])